# IEMS 450-2 Programming Assignment 1 

## (Unconstrained Quadratic Programming)

Created: Feb 3, 2023

Author: Jonathan Bosnich

Purpose: Programming Assigment #1 for Nonlinear Optimization (IEMS 450-2)

Description: 
The overall goal of this program is to compare and contrast
different unconstrained optimization methods on a variety of objective
functions and initial conditions. For each of the four objective
functions given in the assignment description, this program uses every
combination of search direction (steepest descent, Newton's method,
and a Hessian modification) along with three different line search
methods (Armijo backtracking and two variations of Goldsteins 
line search). The results of these numerical experiments can be found
in the cells below the 'Numerical Experiments' heading.

In [702]:
# Import numpy for numerical computations
import numpy as np

### Initialize options for Newton's algorithm

In [703]:
def minimizeObjInitOptions():
    '''
    Initialize algorithm options with default values

    Return values:
        options:
            This is a dictionary with fields that correspond to algorithmic
            options of our method.  In particular:

            max_iter:
                Maximum number of iterations
            tol:
                Convergence tolerance
            step_type:
                Different ways to calculate the search direction:
               'steepest_descent'
               'newton'
               'hessian_modification'
            linesearch:
               Different ways to calculate the step size:
               'backtracking'
               'goldstein'
            init_alpha:
                first trial step size to attempt during line search
            suff_decrease_c1:
                coefficient in Armijo sufficient decrease condition
            goldstein_c1:
                coefficient in Goldstein sufficient decrease condition
            goldstein_c2:
                coefficient in Goldstein sufficient increase condition
            rho:
                scalar > 1 for Goldstein algorithm
            exponent:
                the exponent on the first term of the 2nd objective
                function given to us for the assignment 
            output_level:
                Amount of output printed
                0: No output
                1: Only summary information
                2: One line per iteration (good for debugging)
    '''
    # Create options dictionary with default values
    options = {}

    # General algorithm options
    options['max_iter'] = 1e6
    options['tol'] = 1e-6
    options['output_level'] = 2

    # Linesearch options
    options['linesearch'] = 'backtracking'
    options['init_alpha'] = 1.
    options['suff_decrease_c1'] = 1e-4
    options['goldstein_c1'] = 0.25
    options['goldstein_c2'] = 0.75
    options['rho'] = 1.5

    # Search direction option
    options['step_type'] = 'newton'

    # Objective function options
    options['obj_function'] = 'rosenbrock'
    options['exponent'] = 2

    return options

### Rosenbrock objective function

In [704]:
class Rosenbrock:
    '''
    Implementation of the Rosenbrock objective function

    f(x1, x2) = a*(x2 - x1**2)**2 + (b - x1)**2

    Parameters:
        a: scalar, set to a=100 for this assignment
        b: scalar, set to b=1 for this assignment

    Return Methods:
        value: scalar, returns value of Rosenbrock function at x
        gradient: 2x1 array, returns gradient of Rosenbrock function at x
        hessian: 2x2 array, returns hessian of Rosenbrock function at x
    '''

    def __init__(self, a=100.0, b=1.0):
        '''
        Initialize object with parameters a and b in the formula
        '''
        self._a = a
        self._b = b

    def value(self, x):
        '''
        Compute value of objective function at point x=(x1, x2)
        '''
        a = self._a
        b = self._b
        val = a*(x[1] - x[0]**2)**2 + (b - x[0])**2
        return val

    def gradient(self, x):
        '''
        Compute gradient of objective function at point x=(x1, x2)
        '''
        a = self._a
        b = self._b
        partial_wrt_x1 = -4*a*x[0]*(x[1] - x[0]**2) - 2*(b - x[0])
        partial_wrt_x2 = 2*a*(x[1] - x[0]**2)
        grad = np.array([partial_wrt_x1, partial_wrt_x2])
        return grad

    def hessian(self, x):
        '''
        Compute Hessian of objective function at point x=(x1, x2)
        '''
        a = self._a
        partial_wrt_x1x1 = -4*a*x[1] + 12*a*x[0]**2 + 2
        partial_wrt_x2x2 = 2*a
        partial_wrt_x1x2 = -4*a*x[0]  # This is equal to the 2nd-order partial wrt x2 and x1
        hess = np.array([[partial_wrt_x1x1, partial_wrt_x1x2], [partial_wrt_x1x2, partial_wrt_x2x2]])
        return hess

###  Other objective function

In [705]:
class OtherFunc:
    '''
    Implementation of the second objective function given in the assignment

    f(x1, x2) = (x1-1)^a + (e^x2-1)/(e^x2+1) + 0.1e^-x2

    Parameters:
        a: integer, in this assignment a=2 or a=4

    Return Methods:
        value: scalar, returns value of function at x
        gradient: 2x1 array, returns gradient of function at x
        hessian: 2x2 array, returns hessian of function at x
    '''

    def __init__(self, options):
        '''
        Initialize object with parameters a in the formula
        '''
        self._a = options['exponent']  # Retrieve from options dictionary

    def value(self, x):
        '''
        Compute value of objective function at point x=(x1, x2)
        '''
        a = self._a
        val = (x[0] - 1)**a + (np.exp(x[1])-1)/(np.exp(x[1])+1) + 0.1*np.exp(-x[1])
        return val

    def gradient(self, x):
        '''
        Compute gradient of objective function at point x=(x1, x2)
        '''
        a = self._a
        partial_wrt_x1 = a*(x[0] - 1)**(a-1)
        partial_wrt_x2 = 2*np.exp(x[1])/(np.exp(x[1])+1)**2 - 0.1*np.exp(-x[1])
        grad = np.array([partial_wrt_x1, partial_wrt_x2])
        return grad

    def hessian(self, x):
        '''
        Compute Hessian of objective function at point x=(x1, x2)
        '''
        a = self._a
        partial_wrt_x1x1 = a*(a-1)*(x[0] - 1)**(a-2)
        partial_wrt_x2x2 = 2*np.exp(x[1])*(-1*np.exp(x[1]) + 1)/(np.exp(x[1]) + 1)**3 + 0.1*np.exp(-x[1])
        partial_wrt_x1x2 = 0  # This is equal to the 2nd-order partial wrt x2 and x1
        hess = np.array([[partial_wrt_x1x1, partial_wrt_x1x2], [partial_wrt_x1x2, partial_wrt_x2x2]])
        return hess

### Backtracking line search

In [706]:
def backtracking(objFunc, x_k, p_k, options):
    '''
    The backtracking line search halves the step size until the sufficient
    decrease condition is satisfied, and returns that step size

    Parameters:
        objFunc: object, defines the objective function with methods
            val(): value of objective function
            grad(): gradient of objective function
            hess(): hessian of objective function
        x_k: array, k-th iterate
        p_k: array, search direction at k-th iterate
        options: dictionary, contains the parameters
            init_alpha: scalar, initial value of alpha_k
            suff_decrease_c1: scalar in (0,1), used for sufficient decrease condition

    Return:
        alpha_k: scalar, stepsize for the k-th step that satisfies the
                sufficient decrease condition
        loop_evals: int, number of function evals during the line search loop
    '''
    alpha_k = options['init_alpha']
    c1 = options['suff_decrease_c1']

    val = objFunc.value
    grad = objFunc.gradient
    
    loop_evals = 0  # Initialize number of function evals
    while val(x_k + alpha_k*p_k) > val(x_k) + c1*alpha_k*grad(x_k).T@p_k:
        alpha_k = 0.5*alpha_k

        loop_evals += 1  # Since there's one function eval per loop (f(x_k) can be saved)
    loop_evals += 1  # Since it still had to check the condition
    return alpha_k, loop_evals

### Goldstein Line Search

In [707]:
def goldstein(objFunc, x_k, p_k, options):
    '''
    The Goldstein line search uses the Goldstein conditions
    (sufficient decrease and sufficient increase) to compute
    an appropriate step size, and then returns that step size

    Parameters:
        objFunc: object, defines the objective function with methods
            val(): value of objective function
            grad(): gradient of objective function
            hess(): hessian of objective function
        x_k: array, k-th iterate
        p_k: array, search direction at k-th iterate
        options: dictionary, contains the parameters
            init_alpha: scalar, initial value of alpha_k
            goldstein_c1: scalar in (0,1) s.t. c1 < c2, used for sufficient decrease condition
            goldstein_c2: scalar in (0,1) s.t. c1 < c2, used for sufficient increase condition
            rho: scalar > 1, used to reposition initial alpha_L and alpha_U s.t. the sufficient
                            increase condition is met

    Return:
        alpha_U: scalar, step size for the k-th step that satisfies the Goldstein conditions
        loop_evals: int, number of function evals during the line search loop
    '''
    # Load Goldstein paramets
    c1 = options['goldstein_c1']
    c2 = options['goldstein_c2']
    rho = options['rho']

    # Set lower and upper bounds on alpha_k
    alpha_L = 0
    alpha_U = options['init_alpha']

    val = objFunc.value
    grad = objFunc.gradient

    loop_evals = 0  # Initialize number of function evals 
    
    while val(x_k + alpha_U*p_k) < val(x_k) + c2*alpha_U*grad(x_k).T@p_k:
        alpha_L = alpha_U
        alpha_U = rho*alpha_U

        loop_evals += 1  # One function eval in this condition
    loop_evals += 1  # For when the while loop didn't hold (one eval still happened)

    while val(x_k + alpha_U*p_k) > val(x_k) + c1*alpha_U*grad(x_k).T@p_k:
        alpha_avg = 0.5*(alpha_U + alpha_L)
        loop_evals += 1  # One function eval in this condition
        
        if val(x_k + alpha_avg*p_k) >= val(x_k) + c2*alpha_avg*grad(x_k).T@p_k:
            alpha_U = alpha_avg

            loop_evals += 1  # One function eval in this condition (either counted here)
        else:
            alpha_L = alpha_avg

            loop_evals += 1  # (or here)
    loop_evals += 1  # For when the while loop didn't hold (one eval still happened)
    return alpha_U, loop_evals

### Search direction using a Hessian modification 

In [708]:
def hess_modification(x_k, objFunc):
    '''
    This algorithm first modifies the Hessian s.t. it becomes
    positive definite (if it wasn't already) by adding positive
    scalar multiples of the identity.

    Since the modified Hessian is positive definite iff it can
    be Cholesky factorized, we then compute the Cholesky
    factorization and use it to solve for the new search direction.

    Parameters:
        objFunc: object, defines the objective function with methods
            val(): value of objective function
            grad(): gradient of objective function
            hess(): hessian of objective function
        x_k: array, k-th iterate

    Returns:
        new_dir: array, new search direction for k-th step
    '''
    beta = 1e-4  # algorithm parameter value specified in assignment

    hess = objFunc.hessian(x_k)  # load the true Hessian value

    # Find minimum diagonal element of hessian
    min_diag = np.diagonal(hess).min()

    # Intialize tau, the positive number that will scale the identity
    if min_diag > 0:
        tau = 0
    else:
        tau = -1*min_diag + beta

    CholeskyFact = 0  # Flag to determine when the hessian is succesfully modified
    while CholeskyFact == 0:
        hess_mod = hess + tau*np.eye(len(hess))  # Modify the Hessian
        try:
            L = np.linalg.cholesky(hess_mod)  # If possible, gives Cholesky factorization
            CholeskyFact = 1  # exit loop
        except:
            tau = max([2*tau, beta])

    # Now, solve for the search direction using the Cholesky factorization
    y = np.linalg.solve(L, -1*objFunc.gradient(x_k))
    new_dir = np.linalg.solve(L.T, y)

    # Note: since the hessian is 2x2, it would be quite easy to invert,
    # but I want this code to be compatible with higher dimension problems

    # Another note: np.linalg.solve doesn't compute the matrix inverse;
    # it does a form of LU decomposition
    return new_dir, tau


### Line Search Algorithm

In [709]:
def minimizeObjective(x_start, objFunc, options):
    '''
    Optimization method for unconstrained optimization.

    This line search algorithm will use search directions
    and step sizes to compute sequences of iterates that will
    hopefully converge to a fixed point. However, there are 
    safeguards in place in case something goes awry.

    Input arguments:
        x_start:
            Starting point
        objFunc:
            Objective function object with the following methods
                val = value(x)
                    returns value of objective function at x
                grad = gradient(x)
                    returns gradient of objective function at x
                hess = hessian(x)
                    return Hessian of objective function at x
        options:
            This is a dictionary with options for the algorithm.
            For details see the minimizeObjInitOptions function.

    Return values:
        status:
           Return code indicating reason for termination:
            0:  Optimal solution found (convergence tolerance satisfied)
           -1:  Maximum number of iterations exceeded
           -2:  Search direction is not a descent direction
          -99:  Unknown error (bug?)
        x_sol:
            Approximate critical point (or last iterate if there is a failure)
        f_sol:
            objective function value at x_sol
        stats:
            Dictionary with statistics for the run.  Its fields are
                norm_grad      Norm of gradient at final iterate
                num_iter       Number of iterations taken
                num_func_evals Number of function evaluations needed
    '''

    # Initialize iteration counter
    iter_count = 0

    # Initialize return flag (set to -99 so that we do not accidentally
    # declare success)
    status = -99
    
    # Get parameters out put the options dictionary
    max_iter = options['max_iter']
    tol = options['tol']
    step_type = options['step_type']
    linesearch = options['linesearch']
    init_alpha = options['init_alpha']
    output_level = options['output_level']

    # Initialize current iterate (make a copy so as to not alter x_start)
    x_k = np.copy(x_start)

    # Initialize current function value, gradient, Hessian, 
    # and infinity norm of the gradient
    f_k = objFunc.value(x_k)
    grad_k = objFunc.gradient(x_k)
    norm_grad_k = np.linalg.norm(grad_k, np.inf)

    # Initialize counter for function evaluations
    num_func_evals = 1

    # Determine how many variables are in the problem
    num_vars = len(x_start)

    # Initialize search direction and its length to zero
    p_k = np.zeros(num_vars)
    norm_pk = 0.0

    # Initialize step size to zero (this is only necessary so that we can print
    alpha_k = 0.0

    # Initialize the counter for the function evaluations needed in a
    # particular iteration
    num_func_it = 0

    # Print header and zero-th iteration for output
    if output_level >= 2:
        # Include tau if a hessian modification will be used
        if step_type == 'hessian_modification':
            output_header = '%6s %23s %9s %9s %9s %6s %9s' % \
                ('iter', 'f', '||p_k||', 'alpha', 'tau', '#func', '||grad_f||')
            print(output_header)
            print('%6i %23.16e %9.2e %9.2e %9.2e %6i %9.2e' %
                (iter_count, f_k, norm_pk, alpha_k, 0., num_func_it, norm_grad_k))
        else:
            output_header = '%6s %23s %9s %9s %6s %9s' % \
                ('iter', 'f', '||p_k||', 'alpha', '#func', '||grad_f||')
            print(output_header)
            print('%6i %23.16e %9.2e %9.2e %6i %9.2e' %
                (iter_count, f_k, norm_pk, alpha_k, num_func_it, norm_grad_k))

    ###########################
    # Beginning of main Loop
    ###########################

    # We continue the main loop until the termination tolerance is met.
    while 1:

        ##############################################################
        # Check termination tests
        ##############################################################
        if norm_grad_k <= tol:
            # Termination tolerance met (i.e., ||grad f(x_k)|| < tol)
            status = 0
            break

        if iter_count >= options['max_iter']:
            # Set flag to indicate the maximum number of iterations has been exceeded
            # This max iteration tolerance was set in the options dictionary initialization
            status = -1
            # The following command says that we now want to leave the current
            # loop (which is the while loop here).  The program execution will
            # resume immediately after the end of the loop
            break

        ##############################################################
        # Compute search direction
        ##############################################################
        if step_type == 'newton':
            p_k = -1*np.linalg.inv(objFunc.hessian(x_k))@objFunc.gradient(x_k)
        elif step_type == 'steepest_descent':
            p_k = -1*objFunc.gradient(x_k)
        elif step_type == 'hessian_modification':
            p_k, tau = hess_modification(x_k, objFunc)
        else:
            raise ValueError('Invalid value for options[step_type]')
        
        # Check if p_k is a descent direction, break if not
        if objFunc.gradient(x_k).T@p_k >= 0:
            status = -2  # raise error if not descent direction
            break

        ##############################################################
        # Perform the line search (backtracking Armijo or Goldstein)
        ##############################################################

        # Compute step size
        if linesearch == 'backtracking':
            alpha_k, loop_evals = backtracking(objFunc, x_k, p_k, options)
        elif linesearch == 'goldstein':
            alpha_k, loop_evals = goldstein(objFunc, x_k, p_k, options)
        else:
            raise ValueError('Invalid value for options[linesearch]')

        # Compute trial point and objective value at trial point
        x_trial = x_k + alpha_k*p_k
        f_trial = objFunc.value(x_trial)
        num_func_it = 1
        num_func_it += loop_evals  # add all the function evals from the linesearch

        # Update iterate
        x_k = np.copy(x_trial)
        f_k = f_trial

        # Compute gradient and its norm at the new iterate
        grad_k = objFunc.gradient(x_k)
        norm_grad_k = np.linalg.norm(grad_k, np.inf)

        # For the output, compute the norm of the step
        norm_pk = np.linalg.norm(p_k, np.inf)

        # Update counter for total number of function evaluations
        num_func_evals += num_func_it

        # Increase the iteration counter
        iter_count += 1

        # Iteration output
        if output_level >= 2:
            # Print the output header every 10 iterations
            if iter_count % 10 == 0:
                print(output_header)
            
            if step_type == 'hessian_modification':
                print('%6i %23.16e %9.2e %9.2e %9.2e %6i %9.2e' %
                    (iter_count, f_k, norm_pk, alpha_k, tau, num_func_it, norm_grad_k))
            else:
                print('%6i %23.16e %9.2e %9.2e %6i %9.2e' %
                    (iter_count, f_k, norm_pk, alpha_k, num_func_it, norm_grad_k))

    ###########################
    # End of main loop
    ###########################

    ###########################
    # Finalize results
    ###########################

    # Set last iterate as the one that is returned, together with its objective
    # value
    x_sol = x_k
    f_sol = f_k

    # Set the statistics
    stats = {}
    stats['num_iter'] = iter_count
    stats['norm_grad'] = norm_grad_k
    stats['num_func_evals'] = num_func_evals

    # Final output message
    if output_level >= 1:
        print('')
        print('||grad|| at final point.........: %g' % norm_grad_k)
        print('Final objective.................: %g' % f_sol)
        print('Number of iterations............: %d' % iter_count)
        print('Number of function evaluations..: %d' % num_func_evals)
        if status == 0:
            print('Exit: Critical point found.')
        elif status == -1:
            print('Exit: Maximum number of iterations (%d) exceeded.' %
                  iter_count)
        elif status == -2:
            print('Exit: Search direction is not a descent direction.')
        elif status == -3:
            print('Exit: Exit: Step size becomes zero.')
        else:
            print('ERROR: Unknown status value: %d\n' % status)

    # Return output arguments
    return status, x_sol, f_sol, stats


# Numerical Experiments

### (1.1) Solve Rosenbrock with steepest descent and Armijo backtracking line search from starting point $x_0 = (1.2, 1.2)^T$

In [710]:
options = minimizeObjInitOptions()
options['step_type'] = 'steepest_descent'
options['linesearch'] = 'backtracking'
options['init_alpha'] = 1.
x_start = np.array([1.2, 1.2])
objFunc = Rosenbrock()

status, x_sol, f_sol, stats = minimizeObjective( x_start, objFunc, options )

  iter                       f   ||p_k||     alpha  #func ||grad_f||
     0  5.7999999999999998e+00  0.00e+00  0.00e+00      0  1.16e+02
     1  4.3097519666189282e-01  1.16e+02  9.77e-04     12  2.81e+01
     2  1.9689420206267062e-02  2.81e+01  9.77e-04     12  3.84e+00
     3  1.2615242780140421e-02  3.84e+00  9.77e-04     12  5.91e-01
     4  1.2412774014682531e-02  5.91e-01  9.77e-04     12  1.39e-01
     5  1.2400369865755474e-02  1.39e-01  1.95e-03     11  1.43e-01
     6  1.2390893483147853e-02  1.43e-01  1.95e-03     11  2.15e-01
     7  1.2386536095077649e-02  2.15e-01  1.95e-03     11  1.97e-01
     8  1.2351382060191783e-02  1.97e-01  9.77e-04     12  7.51e-02
     9  1.2335245359875313e-02  7.51e-02  7.81e-03      9  2.75e-01
  iter                       f   ||p_k||     alpha  #func ||grad_f||
    10  1.2279023224760766e-02  2.75e-01  9.77e-04     12  8.74e-02
    11  1.2262350930776491e-02  8.74e-02  3.91e-03     10  1.65e-01
    12  1.2258791818137197e-02  1.65e-01  1.95

### (1.2) Solve Rosenbrock with steepest descent and Goldstein line search with $\overline{\alpha} = 1$ from starting point $x_0 = (1.2, 1.2)^T$

In [711]:
options = minimizeObjInitOptions()
options['step_type'] = 'steepest_descent'
options['linesearch'] = 'goldstein'
options['init_alpha'] = 1.
x_start = np.array([1.2, 1.2])
objFunc = Rosenbrock()

status, x_sol, f_sol, stats = minimizeObjective( x_start, objFunc, options )

  iter                       f   ||p_k||     alpha  #func ||grad_f||
     0  5.7999999999999998e+00  0.00e+00  0.00e+00      0  1.16e+02
     1  4.3097519666189282e-01  1.16e+02  9.77e-04     23  2.81e+01
     2  1.9689420206267062e-02  2.81e+01  9.77e-04     23  3.84e+00
     3  1.2615242780140421e-02  3.84e+00  9.77e-04     23  5.91e-01
     4  1.2412774014682531e-02  5.91e-01  9.77e-04     23  1.39e-01
     5  1.2400369865755474e-02  1.39e-01  1.95e-03     21  1.43e-01
     6  1.2383405940411480e-02  1.43e-01  9.77e-04     23  7.35e-02
     7  1.2326188549502690e-02  7.35e-02  1.56e-02     15  3.42e-01
     8  1.2247153120964046e-02  3.42e-01  9.77e-04     23  9.80e-02
     9  1.2232446405620817e-02  9.80e-02  1.95e-03     21  1.19e-01
  iter                       f   ||p_k||     alpha  #func ||grad_f||
    10  1.2218789897226351e-02  1.19e-01  1.95e-03     21  1.43e-01
    11  1.2206950238805065e-02  1.43e-01  1.95e-03     21  1.46e-01
    12  1.2189289834428529e-02  1.46e-01  9.77

### (1.3) Solve Rosenbrock with steepest descent and Goldstein line search with $\overline{\alpha} = 0.1$ from starting point $x_0 = (1.2, 1.2)^T$

In [712]:
options = minimizeObjInitOptions()
options['step_type'] = 'steepest_descent'
options['linesearch'] = 'goldstein'
options['init_alpha'] = 0.1
x_start = np.array([1.2, 1.2])
objFunc = Rosenbrock()

status, x_sol, f_sol, stats = minimizeObjective( x_start, objFunc, options )

  iter                       f   ||p_k||     alpha  #func ||grad_f||
     0  5.7999999999999998e+00  0.00e+00  0.00e+00      0  1.16e+02
     1  1.5744607544899283e-02  1.16e+02  7.81e-04     17  2.49e+00
     2  1.2529693235947891e-02  2.49e+00  7.81e-04     17  1.66e-01
     3  1.2506374381977978e-02  1.66e-01  7.81e-04     17  8.94e-02
     4  1.2373752907455300e-02  8.94e-02  5.00e-02      5  7.87e-01
     5  1.2084450959974071e-02  7.87e-01  7.81e-04     17  9.10e-02
     6  1.2068358443612384e-02  9.10e-02  3.13e-03     13  1.48e-01
     7  1.2052734529825188e-02  1.48e-01  1.56e-03     15  1.62e-01
     8  1.2037917386969540e-02  1.62e-01  1.56e-03     15  1.30e-01
     9  1.2023685037787437e-02  1.30e-01  1.56e-03     15  1.28e-01
  iter                       f   ||p_k||     alpha  #func ||grad_f||
    10  1.2009888509014861e-02  1.28e-01  1.56e-03     15  1.17e-01
    11  1.1996410622216387e-02  1.17e-01  1.56e-03     15  1.03e-01
    12  1.1985245262320894e-02  1.03e-01  3.13

### (1.4) Solve Rosenbrock with Newton's method and Armijo backtracking line search from starting point $x_0 = (1.2, 1.2)^T$

In [713]:
options = minimizeObjInitOptions()
options['step_type'] = 'newton'
options['linesearch'] = 'backtracking'
options['init_alpha'] = 1.
x_start = np.array([1.2, 1.2])
objFunc = Rosenbrock()

status, x_sol, f_sol, stats = minimizeObjective( x_start, objFunc, options )

  iter                       f   ||p_k||     alpha  #func ||grad_f||
     0  5.7999999999999998e+00  0.00e+00  0.00e+00      0  1.16e+02
     1  3.8384034418534101e-02  2.30e-01  1.00e+00      2  4.00e-01
     2  1.8762343235565783e-02  4.67e-01  5.00e-01      3  4.39e+00
     3  4.2891830020680309e-03  6.47e-02  1.00e+00      2  6.15e-01
     4  9.0327328664285941e-04  1.11e-01  1.00e+00      2  1.14e+00
     5  1.8514093527971669e-05  1.29e-02  1.00e+00      2  3.25e-02
     6  3.3970388401339911e-08  8.40e-03  1.00e+00      2  7.19e-03
     7  3.2266761890130609e-14  8.26e-05  1.00e+00      2  1.36e-06
     8  1.0882873599015540e-25  3.53e-07  1.00e+00      2  1.29e-11

||grad|| at final point.........: 1.28799e-11
Final objective.................: 1.08829e-25
Number of iterations............: 8
Number of function evaluations..: 18
Exit: Critical point found.


### (1.5) Solve Rosenbrock with Newton's method and Goldstein line search with $\overline{\alpha} = 1$ from starting point $x_0 = (1.2, 1.2)^T$

In [714]:
options = minimizeObjInitOptions()
options['step_type'] = 'newton'
options['linesearch'] = 'goldstein'
options['init_alpha'] = 1.
x_start = np.array([1.2, 1.2])
objFunc = Rosenbrock()

status, x_sol, f_sol, stats = minimizeObjective( x_start, objFunc, options )

  iter                       f   ||p_k||     alpha  #func ||grad_f||
     0  5.7999999999999998e+00  0.00e+00  0.00e+00      0  1.16e+02
     1  3.8384034418534101e-02  2.30e-01  1.00e+00      3  4.00e-01
     2  1.8762343235565783e-02  4.67e-01  5.00e-01      5  4.39e+00
     3  4.2891830020680309e-03  6.47e-02  1.00e+00      3  6.15e-01
     4  9.0327328664285941e-04  1.11e-01  1.00e+00      3  1.14e+00
     5  1.8514093527971669e-05  1.29e-02  1.00e+00      3  3.25e-02
     6  3.3970388401339911e-08  8.40e-03  1.00e+00      3  7.19e-03
     7  3.2266761890130609e-14  8.26e-05  1.00e+00      3  1.36e-06
     8  1.0882873599015540e-25  3.53e-07  1.00e+00      3  1.29e-11

||grad|| at final point.........: 1.28799e-11
Final objective.................: 1.08829e-25
Number of iterations............: 8
Number of function evaluations..: 27
Exit: Critical point found.


### (1.6) Solve Rosenbrock with Newton's method and Goldstein line search with $\overline{\alpha} = 0.1$ from starting point $x_0 = (1.2, 1.2)^T$

In [715]:
options = minimizeObjInitOptions()
options['step_type'] = 'newton'
options['linesearch'] = 'goldstein'
options['init_alpha'] = 0.1
x_start = np.array([1.2, 1.2])
objFunc = Rosenbrock()

status, x_sol, f_sol, stats = minimizeObjective( x_start, objFunc, options )

  iter                       f   ||p_k||     alpha  #func ||grad_f||
     0  5.7999999999999998e+00  0.00e+00  0.00e+00      0  1.16e+02
     1  1.4435039329324775e+00  2.30e-01  5.06e-01      7  5.72e+01
     2  3.8014025707326909e-01  9.93e-02  5.06e-01      7  2.83e+01
     3  1.1850825211266230e-01  2.21e-02  5.06e-01      7  1.41e+01
     4  3.2814461121423819e-02  3.61e-02  7.59e-01      8  3.78e+00
     5  1.5046444175524505e-02  1.48e-01  7.59e-01      8  2.17e+00
     6  5.6732810755952458e-03  1.33e-01  7.59e-01      8  1.51e+00
     7  1.6535583986739359e-03  8.53e-02  7.59e-01      8  8.05e-01
     8  3.3013569550533476e-04  5.44e-02  7.59e-01      8  3.77e-01
     9  4.1553040478033035e-05  2.71e-02  7.59e-01      8  1.37e-01
  iter                       f   ||p_k||     alpha  #func ||grad_f||
    10  3.4236013820216877e-06  1.04e-02  7.59e-01      8  3.99e-02
    11  8.6390385950913543e-07  3.07e-03  5.06e-01      7  2.00e-02
    12  2.1434015207962652e-07  1.56e-03  5.06

### (1.7) Solve Rosenbrock with Hessian modification and Armijo backtracking line search from starting point $x_0 = (1.2, 1.2)^T$

In [716]:
options = minimizeObjInitOptions()
options['step_type'] = 'hessian_modification'
options['linesearch'] = 'backtracking'
options['init_alpha'] = 1.
x_start = np.array([1.2, 1.2])
objFunc = Rosenbrock()

status, x_sol, f_sol, stats = minimizeObjective( x_start, objFunc, options )

  iter                       f   ||p_k||     alpha       tau  #func ||grad_f||
     0  5.7999999999999998e+00  0.00e+00  0.00e+00  0.00e+00      0  1.16e+02
     1  3.8384034418534101e-02  2.30e-01  1.00e+00  0.00e+00      2  4.00e-01
     2  1.8762343235565360e-02  4.67e-01  5.00e-01  0.00e+00      3  4.39e+00
     3  4.2891830020682815e-03  6.47e-02  1.00e+00  0.00e+00      2  6.15e-01
     4  9.0327328664250835e-04  1.11e-01  1.00e+00  0.00e+00      2  1.14e+00
     5  1.8514093527986807e-05  1.29e-02  1.00e+00  0.00e+00      2  3.25e-02
     6  3.3970388401295210e-08  8.40e-03  1.00e+00  0.00e+00      2  7.19e-03
     7  3.2266761890130609e-14  8.26e-05  1.00e+00  0.00e+00      2  1.36e-06
     8  1.0882873599015540e-25  3.53e-07  1.00e+00  0.00e+00      2  1.29e-11

||grad|| at final point.........: 1.28799e-11
Final objective.................: 1.08829e-25
Number of iterations............: 8
Number of function evaluations..: 18
Exit: Critical point found.


### (1.8) Solve Rosenbrock with Hessian modification and Goldstein line search with $\overline{\alpha} = 1$ from starting point $x_0 = (1.2, 1.2)^T$

In [717]:
options = minimizeObjInitOptions()
options['step_type'] = 'hessian_modification'
options['linesearch'] = 'goldstein'
options['init_alpha'] = 1.
x_start = np.array([1.2, 1.2])
objFunc = Rosenbrock()

status, x_sol, f_sol, stats = minimizeObjective( x_start, objFunc, options )

  iter                       f   ||p_k||     alpha       tau  #func ||grad_f||
     0  5.7999999999999998e+00  0.00e+00  0.00e+00  0.00e+00      0  1.16e+02
     1  3.8384034418534101e-02  2.30e-01  1.00e+00  0.00e+00      3  4.00e-01
     2  1.8762343235565360e-02  4.67e-01  5.00e-01  0.00e+00      5  4.39e+00
     3  4.2891830020682815e-03  6.47e-02  1.00e+00  0.00e+00      3  6.15e-01
     4  9.0327328664250835e-04  1.11e-01  1.00e+00  0.00e+00      3  1.14e+00
     5  1.8514093527986807e-05  1.29e-02  1.00e+00  0.00e+00      3  3.25e-02
     6  3.3970388401295210e-08  8.40e-03  1.00e+00  0.00e+00      3  7.19e-03
     7  3.2266761890130609e-14  8.26e-05  1.00e+00  0.00e+00      3  1.36e-06
     8  1.0882873599015540e-25  3.53e-07  1.00e+00  0.00e+00      3  1.29e-11

||grad|| at final point.........: 1.28799e-11
Final objective.................: 1.08829e-25
Number of iterations............: 8
Number of function evaluations..: 27
Exit: Critical point found.


### (1.9) Solve Rosenbrock with Hessian modification and Goldstein line search with $\overline{\alpha} = 0.1$ from starting point $x_0 = (1.2, 1.2)^T$

In [718]:
options = minimizeObjInitOptions()
options['step_type'] = 'hessian_modification'
options['linesearch'] = 'goldstein'
options['init_alpha'] = 0.1
x_start = np.array([1.2, 1.2])
objFunc = Rosenbrock()

status, x_sol, f_sol, stats = minimizeObjective( x_start, objFunc, options )

  iter                       f   ||p_k||     alpha       tau  #func ||grad_f||
     0  5.7999999999999998e+00  0.00e+00  0.00e+00  0.00e+00      0  1.16e+02
     1  1.4435039329324721e+00  2.30e-01  5.06e-01  0.00e+00      7  5.72e+01
     2  3.8014025707327165e-01  9.93e-02  5.06e-01  0.00e+00      7  2.83e+01
     3  1.1850825211266230e-01  2.21e-02  5.06e-01  0.00e+00      7  1.41e+01
     4  3.2814461121424804e-02  3.61e-02  7.59e-01  0.00e+00      8  3.78e+00
     5  1.5046444175524150e-02  1.48e-01  7.59e-01  0.00e+00      8  2.17e+00
     6  5.6732810755952380e-03  1.33e-01  7.59e-01  0.00e+00      8  1.51e+00
     7  1.6535583986740602e-03  8.53e-02  7.59e-01  0.00e+00      8  8.05e-01
     8  3.3013569550531855e-04  5.44e-02  7.59e-01  0.00e+00      8  3.77e-01
     9  4.1553040478035542e-05  2.71e-02  7.59e-01  0.00e+00      8  1.37e-01
  iter                       f   ||p_k||     alpha       tau  #func ||grad_f||
    10  3.4236013820224018e-06  1.04e-02  7.59e-01  0.00e+00  

### (2.1) Solve Rosenbrock with steepest descent and Armijo backtracking line search from starting point $x_0 = (-1.2, 1)^T$

In [719]:
options = minimizeObjInitOptions()
options['step_type'] = 'steepest_descent'
options['linesearch'] = 'backtracking'
options['init_alpha'] = 1.
x_start = np.array([-1.2, 1])
objFunc = Rosenbrock()

status, x_sol, f_sol, stats = minimizeObjective( x_start, objFunc, options )

  iter                       f   ||p_k||     alpha  #func ||grad_f||
     0  2.4199999999999996e+01  0.00e+00  0.00e+00      0  2.16e+02
     1  5.1011126637109570e+00  2.16e+02  9.77e-04     12  3.83e+01
     2  5.0470111376546214e+00  3.83e+01  1.95e-03     11  4.19e+01
     3  4.1140390714609625e+00  4.19e+01  9.77e-04     12  2.81e+00
     4  4.1080850212978168e+00  2.81e+00  1.95e-03     11  3.33e+00
     5  4.1021527140761496e+00  3.33e+00  1.95e-03     11  2.88e+00
     6  4.0961281680729726e+00  2.88e+00  1.95e-03     11  3.45e+00
     7  4.0901246018753641e+00  3.45e+00  1.95e-03     11  2.93e+00
     8  4.0840108684295426e+00  2.93e+00  1.95e-03     11  3.53e+00
     9  4.0779179741546772e+00  3.53e+00  1.95e-03     11  2.96e+00
  iter                       f   ||p_k||     alpha  #func ||grad_f||
    10  4.0717040782953413e+00  2.96e+00  1.95e-03     11  3.55e+00
    11  4.0655117295061824e+00  3.55e+00  1.95e-03     11  2.96e+00
    12  4.0591966541883666e+00  2.96e+00  1.95

### (2.2) Solve Rosenbrock with steepest descent and Goldstein line search with $\overline{\alpha} = 1$ from starting point $x_0 = (-1.2, 1)^T$

In [720]:
options = minimizeObjInitOptions()
options['step_type'] = 'steepest_descent'
options['linesearch'] = 'goldstein'
options['init_alpha'] = 1.
x_start = np.array([-1.2, 1])
objFunc = Rosenbrock()

status, x_sol, f_sol, stats = minimizeObjective( x_start, objFunc, options )

  iter                       f   ||p_k||     alpha  #func ||grad_f||
     0  2.4199999999999996e+01  0.00e+00  0.00e+00      0  2.16e+02
     1  5.1011126637109570e+00  2.16e+02  9.77e-04     23  3.83e+01
     2  4.1194159970828759e+00  3.83e+01  9.77e-04     23  2.11e+00
     3  4.1127001314633720e+00  2.11e+00  3.91e-03     19  4.03e+00
     4  6.3508029496247831e-01  4.03e+00  5.00e-01      5  3.14e+01
     5  9.9549477416645813e-04  3.14e+01  9.77e-04     23  1.09e+00
     6  2.7200687464583095e-04  1.09e+00  9.77e-04     23  1.15e-02
     7  2.7000837832947026e-04  1.15e-02  1.56e-02     15  4.01e-02
     8  2.6850008355381618e-04  4.01e-02  9.77e-04     23  1.29e-02
     9  1.1672180189593160e-04  1.29e-02  1.00e+00      3  1.62e-01
  iter                       f   ||p_k||     alpha  #func ||grad_f||
    10  9.9801851018190734e-05  1.62e-01  9.77e-04     23  8.47e-03
    11  9.7656688381787731e-05  8.47e-03  6.25e-02     11  7.03e-02
    12  9.4884700334971528e-05  7.03e-02  9.77

### (2.3) Solve Rosenbrock with steepest descent and Goldstein line search with $\overline{\alpha} = 0.1$ from starting point $x_0 = (-1.2, 1)^T$

In [721]:
options = minimizeObjInitOptions()
options['step_type'] = 'steepest_descent'
options['linesearch'] = 'goldstein'
options['init_alpha'] = 0.1
x_start = np.array([-1.2, 1])
objFunc = Rosenbrock()

status, x_sol, f_sol, stats = minimizeObjective( x_start, objFunc, options )

  iter                       f   ||p_k||     alpha  #func ||grad_f||
     0  2.4199999999999996e+01  0.00e+00  0.00e+00      0  2.16e+02
     1  4.1293887783060059e+00  2.16e+02  7.81e-04     17  2.15e+00
     2  4.1242025902991681e+00  2.15e+00  3.13e-03     13  3.11e+00
     3  4.1157697996223952e+00  3.11e+00  1.56e-03     15  2.73e+00
     4  4.1094796190265050e+00  2.73e+00  1.56e-03     15  2.20e+00
     5  4.1032663910478595e+00  2.20e+00  3.13e-03     13  3.54e+00
     6  4.0955431292706752e+00  3.54e+00  1.56e-03     15  2.44e+00
     7  4.0895053652800515e+00  2.44e+00  1.56e-03     15  1.83e+00
     8  4.0822148665091280e+00  1.83e+00  3.13e-03     13  2.74e+00
     9  4.0751863834951703e+00  2.74e+00  1.56e-03     15  2.19e+00
  iter                       f   ||p_k||     alpha  #func ||grad_f||
    10  4.0698316629392481e+00  2.19e+00  3.13e-03     13  3.11e+00
    11  4.0611339367309540e+00  3.11e+00  1.56e-03     15  2.61e+00
    12  4.0548703136411657e+00  2.61e+00  1.56

### (2.4) Solve Rosenbrock with Newton's method and Armijo backtracking line search from starting point $x_0 = (-1.2, 1)^T$

In [722]:
options = minimizeObjInitOptions()
options['step_type'] = 'newton'
options['linesearch'] = 'backtracking'
options['init_alpha'] = 1.
x_start = np.array([-1.2, 1])
objFunc = Rosenbrock()

status, x_sol, f_sol, stats = minimizeObjective( x_start, objFunc, options )

  iter                       f   ||p_k||     alpha  #func ||grad_f||
     0  2.4199999999999996e+01  0.00e+00  0.00e+00      0  2.16e+02
     1  4.7318843252666083e+00  3.81e-01  1.00e+00      2  4.64e+00
     2  4.0873986620720650e+00  4.56e+00  1.25e-01      5  2.60e+01
     3  3.2286725886219974e+00  2.21e-01  1.00e+00      2  1.06e+01
     4  3.2138980914446202e+00  4.82e-01  1.00e+00      2  2.21e+01
     5  1.9425854206218367e+00  6.70e-02  1.00e+00      2  3.49e+00
     6  1.6001936936471652e+00  7.35e-01  2.50e-01      4  7.42e+00
     7  1.1783895610056250e+00  1.44e-01  1.00e+00      2  4.13e+00
     8  9.2241158192214101e-01  2.08e-01  1.00e+00      2  8.63e+00
     9  5.9748861679012555e-01  8.91e-02  1.00e+00      2  1.59e+00
  iter                       f   ||p_k||     alpha  #func ||grad_f||
    10  4.5262509783031690e-01  2.97e-01  5.00e-01      3  5.21e+00
    11  2.8076243818862784e-01  1.02e-01  1.00e+00      2  1.99e+00
    12  2.1139339642039950e-01  1.77e-01  1.00

### (2.5) Solve Rosenbrock with Newton's method and Goldstein line search with $\overline{\alpha} = 1$ from starting point $x_0 = (-1.2, 1)^T$

In [723]:
options = minimizeObjInitOptions()
options['step_type'] = 'newton'
options['linesearch'] = 'goldstein'
options['init_alpha'] = 1.
x_start = np.array([-1.2, 1])
objFunc = Rosenbrock()

status, x_sol, f_sol, stats = minimizeObjective( x_start, objFunc, options )

  iter                       f   ||p_k||     alpha  #func ||grad_f||
     0  2.4199999999999996e+01  0.00e+00  0.00e+00      0  2.16e+02
     1  4.7318843252666083e+00  3.81e-01  1.00e+00      3  4.64e+00
     2  4.0873986620720650e+00  4.56e+00  1.25e-01      9  2.60e+01
     3  3.2286725886219974e+00  2.21e-01  1.00e+00      3  1.06e+01
     4  2.7678258645542266e+00  4.82e-01  5.00e-01      5  1.25e+01
     5  2.1787222901327086e+00  2.01e-01  1.00e+00      3  9.17e+00
     6  1.6696781327914283e+00  1.72e-01  1.00e+00      3  5.88e+00
     7  1.2682327687529809e+00  1.83e-01  1.00e+00      3  6.68e+00
     8  9.1347221877088669e-01  1.40e-01  1.00e+00      3  3.92e+00
     9  6.8634064394134042e-01  1.90e-01  1.00e+00      3  7.24e+00
  iter                       f   ||p_k||     alpha  #func ||grad_f||
    10  4.3542326889276284e-01  9.05e-02  1.00e+00      3  1.64e+00
    11  3.1960367415063490e-01  2.48e-01  5.00e-01      5  3.90e+00
    12  1.9211959343593088e-01  1.21e-01  1.00

### (2.6) Solve Rosenbrock with Newton's method and Goldstein line search with $\overline{\alpha} = 0.1$ from starting point $x_0 = (-1.2, 1)^T$

In [724]:
options = minimizeObjInitOptions()
options['step_type'] = 'newton'
options['linesearch'] = 'goldstein'
options['init_alpha'] = 0.1
x_start = np.array([-1.2, 1])
objFunc = Rosenbrock()

status, x_sol, f_sol, stats = minimizeObjective( x_start, objFunc, options )

  iter                       f   ||p_k||     alpha  #func ||grad_f||
     0  2.4199999999999996e+01  0.00e+00  0.00e+00      0  2.16e+02
     1  9.5116578333566189e+00  3.81e-01  5.06e-01      7  1.08e+02
     2  5.8424241866918525e+00  1.01e-01  5.06e-01      7  5.45e+01
     3  4.4654255714920525e+00  1.15e-01  7.59e-01      8  1.78e+01
     4  3.8079224215739562e+00  5.97e-01  7.59e-01      8  2.30e+01
     5  3.1484463397159197e+00  2.14e-01  7.59e-01      8  1.17e+01
     6  2.6354573384818445e+00  3.84e-01  7.59e-01      8  1.39e+01
     7  2.1247131313559491e+00  1.42e-01  7.59e-01      8  7.01e+00
     8  1.7341659711130826e+00  2.52e-01  7.59e-01      8  8.46e+00
     9  1.3564179309916371e+00  1.32e-01  7.59e-01      8  4.04e+00
  iter                       f   ||p_k||     alpha  #func ||grad_f||
    10  1.0696153113924436e+00  2.28e-01  7.59e-01      8  6.94e+00
    11  8.0528453309017478e-01  1.23e-01  7.59e-01      8  3.41e+00
    12  6.0551688660939351e-01  2.00e-01  7.59

### (2.7) Solve Rosenbrock with Hessian modification and Armijo backtracking line search from starting point $x_0 = (-1.2, 1)^T$

In [725]:
options = minimizeObjInitOptions()
options['step_type'] = 'hessian_modification'
options['linesearch'] = 'backtracking'
options['init_alpha'] = 1.
x_start = np.array([-1.2, 1])
objFunc = Rosenbrock()

status, x_sol, f_sol, stats = minimizeObjective( x_start, objFunc, options )

  iter                       f   ||p_k||     alpha       tau  #func ||grad_f||
     0  2.4199999999999996e+01  0.00e+00  0.00e+00  0.00e+00      0  2.16e+02
     1  4.7318843252666083e+00  3.81e-01  1.00e+00  0.00e+00      2  4.64e+00
     2  4.0873986620721858e+00  4.56e+00  1.25e-01  0.00e+00      5  2.60e+01
     3  3.2286725886219330e+00  2.21e-01  1.00e+00  0.00e+00      2  1.06e+01
     4  3.2138980914476294e+00  4.82e-01  1.00e+00  0.00e+00      2  2.21e+01
     5  1.9425854206214150e+00  6.70e-02  1.00e+00  0.00e+00      2  3.49e+00
     6  1.6001936936468122e+00  7.35e-01  2.50e-01  0.00e+00      4  7.42e+00
     7  1.1783895610050350e+00  1.44e-01  1.00e+00  0.00e+00      2  4.13e+00
     8  9.2241158192373707e-01  2.08e-01  1.00e+00  0.00e+00      2  8.63e+00
     9  5.9748861678964327e-01  8.91e-02  1.00e+00  0.00e+00      2  1.59e+00
  iter                       f   ||p_k||     alpha       tau  #func ||grad_f||
    10  4.5262509783023303e-01  2.97e-01  5.00e-01  0.00e+00  

### (2.8) Solve Rosenbrock with Hessian modification and Goldstein line search with $\overline{\alpha} = 1$ from starting point $x_0 = (-1.2, 1)^T$

In [726]:
options = minimizeObjInitOptions()
options['step_type'] = 'hessian_modification'
options['linesearch'] = 'goldstein'
options['init_alpha'] = 1.
x_start = np.array([-1.2, 1])
objFunc = Rosenbrock()

status, x_sol, f_sol, stats = minimizeObjective( x_start, objFunc, options )

  iter                       f   ||p_k||     alpha       tau  #func ||grad_f||
     0  2.4199999999999996e+01  0.00e+00  0.00e+00  0.00e+00      0  2.16e+02
     1  4.7318843252666083e+00  3.81e-01  1.00e+00  0.00e+00      3  4.64e+00
     2  4.0873986620721858e+00  4.56e+00  1.25e-01  0.00e+00      9  2.60e+01
     3  3.2286725886219330e+00  2.21e-01  1.00e+00  0.00e+00      3  1.06e+01
     4  2.7678258645540610e+00  4.82e-01  5.00e-01  0.00e+00      5  1.25e+01
     5  2.1787222901323502e+00  2.01e-01  1.00e+00  0.00e+00      3  9.17e+00
     6  1.6696781327913921e+00  1.72e-01  1.00e+00  0.00e+00      3  5.88e+00
     7  1.2682327687523378e+00  1.83e-01  1.00e+00  0.00e+00      3  6.68e+00
     8  9.1347221877086648e-01  1.40e-01  1.00e+00  0.00e+00      3  3.92e+00
     9  6.8634064393857863e-01  1.90e-01  1.00e+00  0.00e+00      3  7.24e+00
  iter                       f   ||p_k||     alpha       tau  #func ||grad_f||
    10  4.3542326889280963e-01  9.05e-02  1.00e+00  0.00e+00  

### (2.9) Solve Rosenbrock with Hessian modification and Goldstein line search with $\overline{\alpha} = 0.1$ from starting point $x_0 = (-1.2, 1)^T$

In [727]:
options = minimizeObjInitOptions()
options['step_type'] = 'hessian_modification'
options['linesearch'] = 'goldstein'
options['init_alpha'] = 0.1
x_start = np.array([-1.2, 1])
objFunc = Rosenbrock()

status, x_sol, f_sol, stats = minimizeObjective( x_start, objFunc, options )

  iter                       f   ||p_k||     alpha       tau  #func ||grad_f||
     0  2.4199999999999996e+01  0.00e+00  0.00e+00  0.00e+00      0  2.16e+02
     1  9.5116578333565975e+00  3.81e-01  5.06e-01  0.00e+00      7  1.08e+02
     2  5.8424241866918560e+00  1.01e-01  5.06e-01  0.00e+00      7  5.45e+01
     3  4.4654255714920517e+00  1.15e-01  7.59e-01  0.00e+00      8  1.78e+01
     4  3.8079224215739438e+00  5.97e-01  7.59e-01  0.00e+00      8  2.30e+01
     5  3.1484463397159228e+00  2.14e-01  7.59e-01  0.00e+00      8  1.17e+01
     6  2.6354573384818432e+00  3.84e-01  7.59e-01  0.00e+00      8  1.39e+01
     7  2.1247131313559522e+00  1.42e-01  7.59e-01  0.00e+00      8  7.01e+00
     8  1.7341659711130821e+00  2.52e-01  7.59e-01  0.00e+00      8  8.46e+00
     9  1.3564179309916400e+00  1.32e-01  7.59e-01  0.00e+00      8  4.04e+00
  iter                       f   ||p_k||     alpha       tau  #func ||grad_f||
    10  1.0696153113924451e+00  2.28e-01  7.59e-01  0.00e+00  

### (3.1) Solve $$f(x_1, x_2) = (x_1-1)^2 + \frac{e^{x_2} - 1}{e^{x_2} + 1} + 0.1e^{-x_2}$$ with steepest descent and Armijo backtracking line search from starting point $x_0 = (-1, 1)^T$

In [728]:
options = minimizeObjInitOptions()
options['step_type'] = 'steepest_descent'
options['linesearch'] = 'backtracking'
options['init_alpha'] = 1.
options['exponent'] = 2
x_start = np.array([-1, 1])
objFunc = OtherFunc(options)

status, x_sol, f_sol, stats = minimizeObjective( x_start, objFunc, options )

  iter                       f   ||p_k||     alpha  #func ||grad_f||
     0  4.4989051013771535e+00  0.00e+00  0.00e+00      0  4.00e+00
     1  4.3636590062970679e+00  4.00e+00  1.00e+00      2  4.00e+00
     2  4.1999553371145595e+00  4.00e+00  1.00e+00      2  4.00e+00
     3  4.0338143323522493e+00  4.00e+00  1.00e+00      2  4.00e+00
     4  3.9057242974335082e+00  4.00e+00  1.00e+00      2  4.00e+00
     5  3.8348823617033445e+00  4.00e+00  1.00e+00      2  4.00e+00
     6  3.8063795862342880e+00  4.00e+00  1.00e+00      2  4.00e+00
     7  3.7974770057474982e+00  4.00e+00  1.00e+00      2  4.00e+00
     8  3.7951389854960529e+00  4.00e+00  1.00e+00      2  4.00e+00
     9 -2.0518702570358294e-01  4.00e+00  5.00e-01      3  2.02e-02
  iter                       f   ||p_k||     alpha  #func ||grad_f||
    10 -2.0548804251187031e-01  2.02e-02  1.00e+00      2  9.52e-03
    11 -2.0555451567693428e-01  9.52e-03  1.00e+00      2  4.43e-03
    12 -2.0556889475610024e-01  4.43e-03  1.00

### (3.2) Solve $$f(x_1, x_2) = (x_1-1)^2 + \frac{e^{x_2} - 1}{e^{x_2} + 1} + 0.1e^{-x_2}$$ with steepest descent and Goldstein line search with $\overline{\alpha} = 1$ from starting point $x_0 = (-1, 1)^T$

In [729]:
options = minimizeObjInitOptions()
options['step_type'] = 'steepest_descent'
options['linesearch'] = 'goldstein'
options['init_alpha'] = 1.
options['exponent'] = 2
x_start = np.array([-1, 1])
objFunc = OtherFunc(options)

status, x_sol, f_sol, stats = minimizeObjective( x_start, objFunc, options )

  iter                       f   ||p_k||     alpha  #func ||grad_f||
     0  4.4989051013771535e+00  0.00e+00  0.00e+00      0  4.00e+00
     1  4.3319372170480464e-01  4.00e+00  5.00e-01      5  3.80e-01
     2  1.4217132562123869e-02  3.80e-01  7.59e+00      8  5.90e-01
     3 -1.9035595118914911e-01  5.90e-01  1.00e+00      3  1.35e-01
     4 -2.0300001471572632e-01  1.35e-01  1.00e+00      3  5.38e-02
     5 -2.0507362597111839e-01  5.38e-02  1.00e+00      3  2.34e-02
     6 -2.0547087876343495e-01  2.34e-02  1.00e+00      3  1.05e-02
     7 -2.0555153998136855e-01  1.05e-02  1.00e+00      3  4.80e-03
     8 -2.0556832804812158e-01  4.80e-03  1.00e+00      3  2.20e-03
     9 -2.0557186082666995e-01  2.20e-03  1.00e+00      3  1.01e-03
  iter                       f   ||p_k||     alpha  #func ||grad_f||
    10 -2.0557260796493571e-01  1.01e-03  1.00e+00      3  4.66e-04
    11 -2.0557276633679789e-01  4.66e-04  1.00e+00      3  2.15e-04
    12 -2.0557279994234551e-01  2.15e-04  1.00

### (3.3) Solve $$f(x_1, x_2) = (x_1-1)^2 + \frac{e^{x_2} - 1}{e^{x_2} + 1} + 0.1e^{-x_2}$$ with steepest descent and Goldstein line search with $\overline{\alpha} = 0.1$ from starting point $x_0 = (-1, 1)^T$

In [730]:
options = minimizeObjInitOptions()
options['step_type'] = 'steepest_descent'
options['linesearch'] = 'goldstein'
options['init_alpha'] = 0.1
options['exponent'] = 2
x_start = np.array([-1, 1])
objFunc = OtherFunc(options)

status, x_sol, f_sol, stats = minimizeObjective( x_start, objFunc, options )

  iter                       f   ||p_k||     alpha  #func ||grad_f||
     0  4.4989051013771535e+00  0.00e+00  0.00e+00      0  4.00e+00
     1  8.7751190910483401e-01  4.00e+00  3.38e-01      6  1.30e+00
     2  4.5170106036545005e-01  1.30e+00  3.38e-01      6  4.22e-01
     3  3.2894476620123847e-01  4.22e-01  5.06e-01      7  4.06e-01
     4 -1.1663667880634054e-01  4.06e-01  5.77e+00     13  3.48e-01
     5 -1.8390071252832718e-01  3.48e-01  7.59e-01      8  1.62e-01
     6 -1.9917035475424683e-01  1.62e-01  7.59e-01      8  8.56e-02
     7 -2.0470265387322595e-01  8.56e-02  1.14e+00      9  2.93e-02
     8 -2.0516810090491033e-01  2.93e-02  5.06e-01      7  2.11e-02
     9 -2.0551530456188288e-01  2.11e-02  1.14e+00      9  7.90e-03
  iter                       f   ||p_k||     alpha  #func ||grad_f||
    10 -2.0556436176223170e-01  7.90e-03  1.14e+00      9  3.01e-03
    11 -2.0557150295768833e-01  3.01e-03  1.14e+00      9  1.16e-03
    12 -2.0557235895224529e-01  1.16e-03  7.59

### (3.4) Solve $$f(x_1, x_2) = (x_1-1)^2 + \frac{e^{x_2} - 1}{e^{x_2} + 1} + 0.1e^{-x_2}$$ with Newton's method and Armijo backtracking line search from starting point $x_0 = (-1, 1)^T$

In [731]:
options = minimizeObjInitOptions()
options['step_type'] = 'newton'
options['linesearch'] = 'backtracking'
options['init_alpha'] = 1.
options['exponent'] = 2
x_start = np.array([-1, 1])
objFunc = OtherFunc(options)

status, x_sol, f_sol, stats = minimizeObjective( x_start, objFunc, options )

  iter                       f   ||p_k||     alpha  #func ||grad_f||
     0  4.4989051013771535e+00  0.00e+00  0.00e+00      0  4.00e+00
     1  9.4216575981054418e-01  2.46e+00  1.00e+00      2  5.60e-02

||grad|| at final point.........: 0.055975
Final objective.................: 0.942166
Number of iterations............: 1
Number of function evaluations..: 3
Exit: Search direction is not a descent direction.


### (3.5) Solve $$f(x_1, x_2) = (x_1-1)^2 + \frac{e^{x_2} - 1}{e^{x_2} + 1} + 0.1e^{-x_2}$$ with Newton's method and Goldstein line search with $\overline{\alpha} = 1$ from starting point $x_0 = (-1, 1)^T$

In [732]:
options = minimizeObjInitOptions()
options['step_type'] = 'newton'
options['linesearch'] = 'goldstein'
options['init_alpha'] = 1.
options['exponent'] = 2
x_start = np.array([-1, 1])
objFunc = OtherFunc(options)

status, x_sol, f_sol, stats = minimizeObjective( x_start, objFunc, options )

  iter                       f   ||p_k||     alpha  #func ||grad_f||
     0  4.4989051013771535e+00  0.00e+00  0.00e+00      0  4.00e+00
     1  9.4216575981054418e-01  2.46e+00  1.00e+00      3  5.60e-02

||grad|| at final point.........: 0.055975
Final objective.................: 0.942166
Number of iterations............: 1
Number of function evaluations..: 4
Exit: Search direction is not a descent direction.


### (3.6) Solve $$f(x_1, x_2) = (x_1-1)^2 + \frac{e^{x_2} - 1}{e^{x_2} + 1} + 0.1e^{-x_2}$$ with Newton's method and Goldstein line search with $\overline{\alpha} = 0.1$ from starting point $x_0 = (-1, 1)^T$

In [733]:
options = minimizeObjInitOptions()
options['step_type'] = 'newton'
options['linesearch'] = 'goldstein'
options['init_alpha'] = 0.1
options['exponent'] = 2
x_start = np.array([-1, 1])
objFunc = OtherFunc(options)

status, x_sol, f_sol, stats = minimizeObjective( x_start, objFunc, options )

  iter                       f   ||p_k||     alpha  #func ||grad_f||
     0  4.4989051013771535e+00  0.00e+00  0.00e+00      0  4.00e+00
     1  1.1297289973002249e+00  2.46e+00  7.59e-01      8  9.62e-01
     2  9.9747142716655990e-01  1.13e+00  5.06e-01      7  4.75e-01
     3  9.7897479063355708e-01  1.07e+00  5.06e-01      7  2.35e-01

||grad|| at final point.........: 0.234647
Final objective.................: 0.978975
Number of iterations............: 3
Number of function evaluations..: 23
Exit: Search direction is not a descent direction.


### (3.7) Solve $$f(x_1, x_2) = (x_1-1)^2 + \frac{e^{x_2} - 1}{e^{x_2} + 1} + 0.1e^{-x_2}$$ with Hessian modification and Armijo backtracking line search from starting point $x_0 = (-1, 1)^T$

In [734]:
options = minimizeObjInitOptions()
options['step_type'] = 'hessian_modification'
options['linesearch'] = 'backtracking'
options['init_alpha'] = 1.
options['exponent'] = 2
x_start = np.array([-1, 1])
objFunc = OtherFunc(options)

status, x_sol, f_sol, stats = minimizeObjective( x_start, objFunc, options )

  iter                       f   ||p_k||     alpha       tau  #func ||grad_f||
     0  4.4989051013771535e+00  0.00e+00  0.00e+00  0.00e+00      0  4.00e+00
     1  4.3422520963530111e+00  3.56e+03  9.77e-04  1.45e-01     12  4.00e+00
     2 -1.4905531518596604e-01  2.00e+00  1.00e+00  0.00e+00      2  2.72e-01
     3 -2.0468364924167781e-01  3.79e-01  1.00e+00  0.00e+00      2  3.14e-02
     4 -2.0557250127084442e-01  5.60e-02  1.00e+00  0.00e+00      2  5.76e-04
     5 -2.0557280900004471e-01  1.07e-03  1.00e+00  0.00e+00      2  2.06e-07

||grad|| at final point.........: 2.06291e-07
Final objective.................: -0.205573
Number of iterations............: 5
Number of function evaluations..: 21
Exit: Critical point found.


C:\Users\jonat\AppData\Local\Temp\ipykernel_6216\228087664.py:27: RuntimeWarning: overflow encountered in exp
  val = (x[0] - 1)**a + (np.exp(x[1])-1)/(np.exp(x[1])+1) + 0.1*np.exp(-x[1])


### (3.8) Solve $$f(x_1, x_2) = (x_1-1)^2 + \frac{e^{x_2} - 1}{e^{x_2} + 1} + 0.1e^{-x_2}$$ with Hessian modification and Goldstein line search with $\overline{\alpha} = 1$ from starting point $x_0 = (-1, 1)^T$

In [735]:
options = minimizeObjInitOptions()
options['step_type'] = 'hessian_modification'
options['linesearch'] = 'goldstein'
options['init_alpha'] = 1.
options['exponent'] = 2
x_start = np.array([-1, 1])
objFunc = OtherFunc(options)

status, x_sol, f_sol, stats = minimizeObjective( x_start, objFunc, options )

  iter                       f   ||p_k||     alpha       tau  #func ||grad_f||
     0  4.4989051013771535e+00  0.00e+00  0.00e+00  0.00e+00      0  4.00e+00
     1  3.8281339574808189e+00  3.56e+03  7.32e-04  1.45e-01     27  4.00e+00
     2 -2.0512447569159609e-01  2.00e+00  1.00e+00  0.00e+00      3  2.22e-02
     3 -2.0557272922361330e-01  4.01e-02  1.00e+00  0.00e+00      3  2.93e-04
     4 -2.0557280900008151e-01  5.44e-04  1.00e+00  0.00e+00      3  5.35e-08

||grad|| at final point.........: 5.34971e-08
Final objective.................: -0.205573
Number of iterations............: 4
Number of function evaluations..: 37
Exit: Critical point found.


C:\Users\jonat\AppData\Local\Temp\ipykernel_6216\228087664.py:27: RuntimeWarning: overflow encountered in exp
  val = (x[0] - 1)**a + (np.exp(x[1])-1)/(np.exp(x[1])+1) + 0.1*np.exp(-x[1])


### (3.9) Solve $$f(x_1, x_2) = (x_1-1)^2 + \frac{e^{x_2} - 1}{e^{x_2} + 1} + 0.1e^{-x_2}$$ with Hessian modification and Goldstein line search with $\overline{\alpha} = 0.1$ from starting point $x_0 = (-1, 1)^T$

In [736]:
options = minimizeObjInitOptions()
options['step_type'] = 'hessian_modification'
options['linesearch'] = 'goldstein'
options['init_alpha'] = 0.1
options['exponent'] = 2
x_start = np.array([-1, 1])
objFunc = OtherFunc(options)

status, x_sol, f_sol, stats = minimizeObjective( x_start, objFunc, options )

  iter                       f   ||p_k||     alpha       tau  #func ||grad_f||
     0  4.4989051013771535e+00  0.00e+00  0.00e+00  0.00e+00      0  4.00e+00
     1  3.8773859153321393e+00  3.56e+03  7.81e-04  1.45e-01     17  4.00e+00
     2  7.9600088378565603e-01  2.00e+00  5.06e-01  0.00e+00      7  1.97e+00
     3  3.9730177022343494e-02  9.87e-01  5.06e-01  0.00e+00      7  9.74e-01
     4 -1.4559249870287538e-01  4.87e-01  5.06e-01  0.00e+00      7  4.81e-01
     5 -1.9092508876366959e-01  2.41e-01  5.06e-01  0.00e+00      7  2.38e-01
     6 -2.0199854262186323e-01  1.19e-01  5.06e-01  0.00e+00      7  1.17e-01
     7 -2.0470102412987451e-01  5.86e-02  5.06e-01  0.00e+00      7  5.79e-02
     8 -2.0536022587398106e-01  2.90e-02  5.06e-01  0.00e+00      7  2.86e-02
     9 -2.0552097728389851e-01  1.43e-02  5.06e-01  0.00e+00      7  1.41e-02
  iter                       f   ||p_k||     alpha       tau  #func ||grad_f||
    10 -2.0556017223471046e-01  7.06e-03  5.06e-01  0.00e+00  

### (4.1) Solve $$f(x_1, x_2) = (x_1-1)^4 + \frac{e^{x_2} - 1}{e^{x_2} + 1} + 0.1e^{-x_2}$$ with steepest descent and Armijo backtracking line search from starting point $x_0 = (-1, 1)^T$

In [737]:
options = minimizeObjInitOptions()
options['step_type'] = 'steepest_descent'
options['linesearch'] = 'backtracking'
options['init_alpha'] = 1.
options['exponent'] = 4
x_start = np.array([-1, 1])
objFunc = OtherFunc(options)

status, x_sol, f_sol, stats = minimizeObjective( x_start, objFunc, options )

  iter                       f   ||p_k||     alpha  #func ||grad_f||
     0  1.6498905101377154e+01  0.00e+00  0.00e+00      0  3.20e+01
     1  1.6482882063045029e+01  3.20e+01  1.25e-01      5  3.20e+01
     2  1.6466288809933442e+01  3.20e+01  1.25e-01      5  3.20e+01
     3  1.6449128607460992e+01  3.20e+01  1.25e-01      5  3.20e+01
     4  1.6431409520249289e+01  3.20e+01  1.25e-01      5  3.20e+01
     5  1.6413145003334797e+01  3.20e+01  1.25e-01      5  3.20e+01
     6  1.6394354468427284e+01  3.20e+01  1.25e-01      5  3.20e+01
     7  1.6375063799186410e+01  3.20e+01  1.25e-01      5  3.20e+01
     8  1.6355305785773144e+01  3.20e+01  1.25e-01      5  3.20e+01
     9  1.6335120446255338e+01  3.20e+01  1.25e-01      5  3.20e+01
  iter                       f   ||p_k||     alpha  #func ||grad_f||
    10  1.6314555201356821e+01  3.20e+01  1.25e-01      5  3.20e+01
    11  1.6293664870084587e+01  3.20e+01  1.25e-01      5  3.20e+01
    12  1.6272511457420400e+01  3.20e+01  1.25

### (4.2) Solve $$f(x_1, x_2) = (x_1-1)^4 + \frac{e^{x_2} - 1}{e^{x_2} + 1} + 0.1e^{-x_2}$$ with steepest descent and Goldstein line search with $\overline{\alpha} = 1$ from starting point $x_0 = (-1, 1)^T$

In [738]:
options = minimizeObjInitOptions()
options['step_type'] = 'steepest_descent'
options['linesearch'] = 'goldstein'
options['init_alpha'] = 1.
options['exponent'] = 4
x_start = np.array([-1, 1])
objFunc = OtherFunc(options)

status, x_sol, f_sol, stats = minimizeObjective( x_start, objFunc, options )

  iter                       f   ||p_k||     alpha  #func ||grad_f||
     0  1.6498905101377154e+01  0.00e+00  0.00e+00      0  3.20e+01
     1  4.9092892983457936e-01  3.20e+01  6.25e-02     11  3.60e-01
     2 -1.2738340136465554e-01  3.60e-01  7.59e+00      8  3.26e-01
     3 -1.9618555133765825e-01  3.26e-01  1.00e+00      3  1.05e-01
     4 -2.0390191690564224e-01  1.05e-01  1.00e+00      3  4.32e-02
     5 -2.0524276828121091e-01  4.32e-02  1.00e+00      3  1.90e-02
     6 -2.0550491564480894e-01  1.90e-02  1.00e+00      3  8.59e-03
     7 -2.0555859592146175e-01  8.59e-03  1.00e+00      3  3.92e-03
     8 -2.0556981017813941e-01  3.92e-03  1.00e+00      3  1.80e-03
     9 -2.0557217401976091e-01  1.80e-03  1.00e+00      3  8.28e-04
  iter                       f   ||p_k||     alpha  #func ||grad_f||
    10 -2.0557267432770326e-01  8.28e-04  1.00e+00      3  3.81e-04
    11 -2.0557278041611682e-01  3.81e-04  1.00e+00      3  1.76e-04
    12 -2.0557280293109476e-01  1.76e-04  1.00

### (4.3) Solve $$f(x_1, x_2) = (x_1-1)^4 + \frac{e^{x_2} - 1}{e^{x_2} + 1} + 0.1e^{-x_2}$$ with steepest descent and Goldstein line search with $\overline{\alpha} = 0.1$ from starting point $x_0 = (-1, 1)^T$

In [739]:
options = minimizeObjInitOptions()
options['step_type'] = 'steepest_descent'
options['linesearch'] = 'goldstein'
options['init_alpha'] = 0.1
options['exponent'] = 4
x_start = np.array([-1, 1])
objFunc = OtherFunc(options)

status, x_sol, f_sol, stats = minimizeObjective( x_start, objFunc, options )

  iter                       f   ||p_k||     alpha  #func ||grad_f||
     0  1.6498905101377154e+01  0.00e+00  0.00e+00      0  3.20e+01
     1  5.1812985990947646e-01  3.20e+01  5.00e-02      5  3.59e-01
     2  6.8927640153067571e-02  3.59e-01  3.84e+00     12  7.97e-01
     3 -4.4745882569828532e-02  7.97e-01  2.25e-01      5  3.13e-01
     4 -1.3570362097650285e-01  3.13e-01  7.59e-01      8  2.39e-01
     5 -2.0088053731176619e-01  2.39e-01  1.71e+00     10  6.57e-02
     6 -2.0454088585500574e-01  6.57e-02  1.14e+00      9  2.77e-02
     7 -2.0524042635226830e-01  2.77e-02  1.14e+00      9  1.11e-02
     8 -2.0543020797225553e-01  1.11e-02  1.71e+00     10  5.20e-03
     9 -2.0550870692425099e-01  5.20e-03  3.84e+00     12  2.83e-03
  iter                       f   ||p_k||     alpha  #func ||grad_f||
    10 -2.0553420529782934e-01  2.83e-03  3.84e+00     12  1.92e-03
    11 -2.0554628474725389e-01  1.92e-03  3.84e+00     12  1.42e-03
    12 -2.0555219239601369e-01  1.42e-03  2.56

### (4.4) Solve $$f(x_1, x_2) = (x_1-1)^4 + \frac{e^{x_2} - 1}{e^{x_2} + 1} + 0.1e^{-x_2}$$ with Newton's method and Armijo backtracking line search from starting point $x_0 = (-1, 1)^T$

In [740]:
options = minimizeObjInitOptions()
options['step_type'] = 'newton'
options['linesearch'] = 'backtracking'
options['init_alpha'] = 1.
options['exponent'] = 4
x_start = np.array([-1, 1])
objFunc = OtherFunc(options)

status, x_sol, f_sol, stats = minimizeObjective( x_start, objFunc, options )

  iter                       f   ||p_k||     alpha  #func ||grad_f||
     0  1.6498905101377154e+01  0.00e+00  0.00e+00      0  3.20e+01
     1  4.1026595869710389e+00  2.46e+00  1.00e+00      2  9.48e+00
     2  1.6040066083156717e+00  1.07e+00  1.00e+00      2  2.81e+00
     3  1.1159708843182841e+00  1.02e+00  1.00e+00      2  8.32e-01
     4  1.0216714903967083e+00  1.01e+00  1.00e+00      2  2.47e-01
     5  1.0038249900249125e+00  1.00e+00  1.00e+00      2  7.31e-02
     6  1.0005877476692704e+00  1.00e+00  1.00e+00      2  2.17e-02
     7  1.0000543489849900e+00  1.00e+00  1.00e+00      2  6.42e-03
     8  9.9998801701091922e-01  1.00e+00  1.00e+00      2  1.90e-03
     9  9.9998797057776645e-01  1.00e+00  2.50e-01      4  1.46e-03

||grad|| at final point.........: 0.00146418
Final objective.................: 0.999988
Number of iterations............: 9
Number of function evaluations..: 21
Exit: Search direction is not a descent direction.


### (4.5) Solve $$f(x_1, x_2) = (x_1-1)^4 + \frac{e^{x_2} - 1}{e^{x_2} + 1} + 0.1e^{-x_2}$$ with Newton's method and Goldstein line search with $\overline{\alpha} = 1$ from starting point $x_0 = (-1, 1)^T$

In [741]:
options = minimizeObjInitOptions()
options['step_type'] = 'newton'
options['linesearch'] = 'goldstein'
options['init_alpha'] = 1.
options['exponent'] = 4
x_start = np.array([-1, 1])
objFunc = OtherFunc(options)

status, x_sol, f_sol, stats = minimizeObjective( x_start, objFunc, options )

  iter                       f   ||p_k||     alpha  #func ||grad_f||
     0  1.6498905101377154e+01  0.00e+00  0.00e+00      0  3.20e+01
     1  4.1026595869710389e+00  2.46e+00  1.00e+00      3  9.48e+00
     2  1.6040066083156717e+00  1.07e+00  1.00e+00      3  2.81e+00
     3  1.1159708843182841e+00  1.02e+00  1.00e+00      3  8.32e-01
     4  1.0216714903967083e+00  1.01e+00  1.00e+00      3  2.47e-01
     5  1.0038249900249125e+00  1.00e+00  1.00e+00      3  7.31e-02
     6  1.0005877476692704e+00  1.00e+00  1.00e+00      3  2.17e-02
     7  1.0000543489849900e+00  1.00e+00  1.00e+00      3  6.42e-03
     8  9.9998801701091922e-01  1.00e+00  1.00e+00      3  1.90e-03
     9  9.9998797057776645e-01  1.00e+00  2.50e-01      7  1.46e-03

||grad|| at final point.........: 0.00146418
Final objective.................: 0.999988
Number of iterations............: 9
Number of function evaluations..: 32
Exit: Search direction is not a descent direction.


### (4.6) Solve $$f(x_1, x_2) = (x_1-1)^4 + \frac{e^{x_2} - 1}{e^{x_2} + 1} + 0.1e^{-x_2}$$ with Newton's method and Goldstein line search with $\overline{\alpha} = 0.1$ from starting point $x_0 = (-1, 1)^T$

In [742]:
options = minimizeObjInitOptions()
options['step_type'] = 'newton'
options['linesearch'] = 'goldstein'
options['init_alpha'] = 0.1
options['exponent'] = 4
x_start = np.array([-1, 1])
objFunc = OtherFunc(options)

status, x_sol, f_sol, stats = minimizeObjective( x_start, objFunc, options )

  iter                       f   ||p_k||     alpha  #func ||grad_f||
     0  1.6498905101377154e+01  0.00e+00  0.00e+00      0  3.20e+01
     1  5.8767783152323538e+00  2.46e+00  7.59e-01      8  1.33e+01
     2  2.5044891418921198e+00  1.13e+00  7.59e-01      8  5.55e+00
     3  1.4616737924041623e+00  1.05e+00  7.59e-01      8  2.31e+00
     4  1.1405702634160564e+00  1.02e+00  7.59e-01      8  9.64e-01
     5  1.0422853368229887e+00  1.01e+00  7.59e-01      8  4.02e-01
     6  1.0124745266995430e+00  1.00e+00  7.59e-01      8  1.67e-01
     7  1.0035614620121083e+00  1.00e+00  7.59e-01      8  6.97e-02
     8  1.0009582724824286e+00  1.00e+00  7.59e-01      8  2.90e-02
     9  1.0002279976501993e+00  1.00e+00  7.59e-01      8  1.21e-02
  iter                       f   ||p_k||     alpha  #func ||grad_f||
    10  1.0000380971467462e+00  1.00e+00  7.59e-01      8  5.04e-03
    11  9.9999648202498925e-01  1.00e+00  7.59e-01      8  2.10e-03
    12  9.9999257124219487e-01  1.00e+00  5.06

### (4.7) Solve $$f(x_1, x_2) = (x_1-1)^4 + \frac{e^{x_2} - 1}{e^{x_2} + 1} + 0.1e^{-x_2}$$ with Hessian modification and Armijo backtracking line search from starting point $x_0 = (-1, 1)^T$

In [743]:
options = minimizeObjInitOptions()
options['step_type'] = 'hessian_modification'
options['linesearch'] = 'backtracking'
options['init_alpha'] = 1.
options['exponent'] = 4
x_start = np.array([-1, 1])
objFunc = OtherFunc(options)

status, x_sol, f_sol, stats = minimizeObjective( x_start, objFunc, options )

  iter                       f   ||p_k||     alpha       tau  #func ||grad_f||
     0  1.6498905101377154e+01  0.00e+00  0.00e+00  0.00e+00      0  3.20e+01
     1  1.6328772600956416e+01  3.56e+03  9.77e-04  1.45e-01     12  3.20e+01
     2  3.0073376788259232e+00  8.00e-01  1.00e+00  0.00e+00      2  9.47e+00
     3  4.1880138661252275e-01  4.44e-01  1.00e+00  0.00e+00      2  2.81e+00
     4 -8.2414963324335733e-02  2.96e-01  1.00e+00  0.00e+00      2  8.32e-01
     5 -1.8124539409703067e-01  1.97e-01  1.00e+00  0.00e+00      2  2.46e-01
     6 -2.0076739371059982e-01  1.32e-01  1.00e+00  0.00e+00      2  7.30e-02
     7 -2.0462359116512413e-01  8.78e-02  1.00e+00  0.00e+00      2  2.16e-02
     8 -2.0538530918083259e-01  5.85e-02  1.00e+00  0.00e+00      2  6.41e-03
     9 -2.0553577199875034e-01  3.90e-02  1.00e+00  0.00e+00      2  1.90e-03
  iter                       f   ||p_k||     alpha       tau  #func ||grad_f||
    10 -2.0556549304920330e-01  2.60e-02  1.00e+00  0.00e+00  

C:\Users\jonat\AppData\Local\Temp\ipykernel_6216\228087664.py:27: RuntimeWarning: overflow encountered in exp
  val = (x[0] - 1)**a + (np.exp(x[1])-1)/(np.exp(x[1])+1) + 0.1*np.exp(-x[1])


### (4.8) Solve $$f(x_1, x_2) = (x_1-1)^4 + \frac{e^{x_2} - 1}{e^{x_2} + 1} + 0.1e^{-x_2}$$ with Hessian modification and Goldstein line search with $\overline{\alpha} = 1$ from starting point $x_0 = (-1, 1)^T$

In [744]:
options = minimizeObjInitOptions()
options['step_type'] = 'hessian_modification'
options['linesearch'] = 'goldstein'
options['init_alpha'] = 1.
options['exponent'] = 4
x_start = np.array([-1, 1])
objFunc = OtherFunc(options)

status, x_sol, f_sol, stats = minimizeObjective( x_start, objFunc, options )

  iter                       f   ||p_k||     alpha       tau  #func ||grad_f||
     0  1.6498905101377154e+01  0.00e+00  0.00e+00  0.00e+00      0  3.20e+01
     1  1.5818023062583203e+01  3.56e+03  7.32e-04  1.45e-01     27  3.20e+01
     2  2.9522933522554160e+00  6.67e-01  1.00e+00  0.00e+00      3  9.47e+00
     3  4.1811474296345036e-01  4.44e-01  1.00e+00  0.00e+00      3  2.81e+00
     4 -8.2375283629797347e-02  2.96e-01  1.00e+00  0.00e+00      3  8.32e-01
     5 -1.8123749534669464e-01  1.97e-01  1.00e+00  0.00e+00      3  2.46e-01
     6 -2.0076583346361193e-01  1.32e-01  1.00e+00  0.00e+00      3  7.30e-02
     7 -2.0462328296818827e-01  8.78e-02  1.00e+00  0.00e+00      3  2.16e-02
     8 -2.0538524830242549e-01  5.85e-02  1.00e+00  0.00e+00      3  6.41e-03
     9 -2.0553575997338597e-01  3.90e-02  1.00e+00  0.00e+00      3  1.90e-03
  iter                       f   ||p_k||     alpha       tau  #func ||grad_f||
    10 -2.0556549067382263e-01  2.60e-02  1.00e+00  0.00e+00  

C:\Users\jonat\AppData\Local\Temp\ipykernel_6216\228087664.py:27: RuntimeWarning: overflow encountered in exp
  val = (x[0] - 1)**a + (np.exp(x[1])-1)/(np.exp(x[1])+1) + 0.1*np.exp(-x[1])


### (4.9) Solve $$f(x_1, x_2) = (x_1-1)^4 + \frac{e^{x_2} - 1}{e^{x_2} + 1} + 0.1e^{-x_2}$$ with Hessian modification and Goldstein line search with $\overline{\alpha} = 0.1$ from starting point $x_0 = (-1, 1)^T$

In [745]:
options = minimizeObjInitOptions()
options['step_type'] = 'hessian_modification'
options['linesearch'] = 'goldstein'
options['init_alpha'] = 0.1
options['exponent'] = 4
x_start = np.array([-1, 1])
objFunc = OtherFunc(options)

status, x_sol, f_sol, stats = minimizeObjective( x_start, objFunc, options )

  iter                       f   ||p_k||     alpha       tau  #func ||grad_f||
     0  1.6498905101377154e+01  0.00e+00  0.00e+00  0.00e+00      0  3.20e+01
     1  1.5866601232440214e+01  3.56e+03  7.81e-04  1.45e-01     17  3.20e+01
     2  4.7786852928534653e+00  6.66e-01  7.59e-01  0.00e+00      8  1.33e+01
     3  1.3428663745436682e+00  4.98e-01  7.59e-01  0.00e+00      8  5.55e+00
     4  2.7603543006825326e-01  3.72e-01  7.59e-01  0.00e+00      8  2.31e+00
     5 -5.5726789569256474e-02  2.78e-01  7.59e-01  0.00e+00      8  9.63e-01
     6 -1.5894670384589255e-01  2.07e-01  7.59e-01  0.00e+00      8  4.01e-01
     7 -1.9106441392166479e-01  1.55e-01  7.59e-01  0.00e+00      8  1.67e-01
     8 -2.0105829720105212e-01  1.16e-01  7.59e-01  0.00e+00      8  6.97e-02
     9 -2.0416804802959859e-01  8.64e-02  7.59e-01  0.00e+00      8  2.90e-02
  iter                       f   ||p_k||     alpha       tau  #func ||grad_f||
    10 -2.0513569560689249e-01  6.45e-02  7.59e-01  0.00e+00  